In [1]:
!pip install pyarrow

Defaulting to user installation because normal site-packages is not writeable
  Using cached pyarrow-12.0.1-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (39.0 MB)

[notice] A new release of pip is available: 23.1.2 -> 23.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [2]:
!pip install lightgbm

Defaulting to user installation because normal site-packages is not writeable
  Using cached lightgbm-4.0.0-py3-none-manylinux_2_28_x86_64.whl (3.0 MB)

[notice] A new release of pip is available: 23.1.2 -> 23.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [3]:
!pip install evidently

Defaulting to user installation because normal site-packages is not writeable
  Using cached evidently-0.4.0-py3-none-any.whl (5.3 MB)
  Using cached statsmodels-0.14.0-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (10.2 MB)
  Using cached nltk-3.8.1-py3-none-any.whl (1.5 MB)
  Using cached umap_learn-0.5.3-py3-none-any.whl
  Using cached pydantic-1.10.11-cp38-cp38-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (3.2 MB)
  Using cached fastapi-0.100.0-py3-none-any.whl (65 kB)
  Using cached uvicorn-0.23.1-py3-none-any.whl (59 kB)
  Using cached typer-0.9.0-py3-none-any.whl (45 kB)
  Using cached rich-13.4.2-py3-none-any.whl (239 kB)
  Using cached iterative_telemetry-0.0.5-py3-none-any.whl (9.3 kB)
  Using cached appdirs-1.4.4-py2.py3-none-any.whl (9.6 kB)
  Using cached filelock-3.12.2-py3-none-any.whl (10 kB)
  Using cached distro-1.8.0-py3-none-any.whl (20 kB)
  Using cached starlette-0.27.0-py3-none-any.whl (66 kB)
  Using cached regex-2023.6.3-cp38-cp38-manylinux_2_17_x8

In [4]:
!pip install shap

Defaulting to user installation because normal site-packages is not writeable
  Using cached shap-0.42.1-cp38-cp38-manylinux_2_12_x86_64.manylinux2010_x86_64.manylinux_2_17_x86_64.manylinux2014_x86_64.whl (550 kB)
  Using cached slicer-0.0.7-py3-none-any.whl (14 kB)
  Using cached cloudpickle-2.2.1-py3-none-any.whl (25 kB)

[notice] A new release of pip is available: 23.1.2 -> 23.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [6]:
import pandas as pd
import numpy as np
import pickle
import shap
import joblib

from evidently.report import Report
from evidently.metric_preset import DataDriftPreset, TargetDriftPreset


In [9]:
model = pickle.load(open("../modeling_SMOTE/model.pkl", "rb"))

In [10]:
df_train = pd.read_parquet("../working/df_application_train.parquet")

In [11]:
df_test = pd.read_parquet("../working/df_application_test.parquet")

In [12]:
shap_values = joblib.load("../modeling_SMOTE/shap_values.joblib")

In [13]:
vals = np.abs(shap_values.values[:,:,1]).mean(0)
feature_importance = pd.DataFrame(
    list(zip(df_test.drop(columns="SK_ID_CURR").columns, vals)),
    columns=['col_name', 'feature_importance_vals']
)
feature_importance.sort_values(by=['feature_importance_vals'], ascending=False, inplace=True)

In [14]:
feature_importance

col_name  feature_importance_vals
72                                 CODE_GENDER_M                 0.328597
25                                  EXT_SOURCE_2                 0.317033
99                    NAME_FAMILY_STATUS_Married                 0.281713
26                                  EXT_SOURCE_3                 0.264389
92                      NAME_INCOME_TYPE_Working                 0.251825
..                                           ...                      ...
144                ORGANIZATION_TYPE_Electricity                 0.000000
145                  ORGANIZATION_TYPE_Emergency                 0.000000
147                      ORGANIZATION_TYPE_Hotel                 0.000000
318                INSTALLMENTS_PAYMENTS_DPD_min                 0.000000
232  PREVIOUS_APPLICATION_DAYS_FIRST_DRAWING_max                 0.000000

[465 rows x 2 columns]

In [15]:
feature_importance.loc[feature_importance["feature_importance_vals"]>=.0333].shape

(80, 2)

In [25]:
feature_importance.loc[feature_importance["feature_importance_vals"]>=0.0333]['feature_importance_vals'].sum()

6.596607432071385

In [17]:
feature_importance['feature_importance_vals'].sum()

10.165028841767167

In [18]:
100 * feature_importance.loc[feature_importance["feature_importance_vals"]>=0.0333]['feature_importance_vals'].sum() / feature_importance['feature_importance_vals'].sum()

64.89511770951925

En prenant les 80 premières features qui expliquent le modèle de manière globale, on peut expliquer 65% des variations du modèle.

On va calculer la prédiction de la feature TARGET sur les datasets df_train et df_test afin de voir si le drift éventuel des features sources engendre un drift au niveau de la cible à prédire.

In [40]:
y_predic_proba = model.predict_proba( df_train.drop(columns=["SK_ID_CURR", "TARGET"]) )
df_train["TARGET"] = np.where(y_predic_proba[:,1]>0.16,1,0)

In [41]:
y_predic_proba = model.predict_proba( df_test.drop(columns=["SK_ID_CURR"]) )
df_test["TARGET"] = np.where(y_predic_proba[:,1]>0.16,1,0)

In [46]:
reference = df_train.loc[:, feature_importance.loc[feature_importance["feature_importance_vals"]>=.0333]["col_name"].to_list() + ["TARGET"] ].sample(frac=1, replace=False)
current = df_test.loc[:, feature_importance.loc[feature_importance["feature_importance_vals"]>=.0333]["col_name"].to_list() + ["TARGET"] ].sample(frac=1, replace=False)

In [47]:
report = Report(metrics=[
    DataDriftPreset(), 
])

report.run(reference_data=reference, current_data=current)


In [44]:
report.save_html("report_data_drift-80.html")

In [45]:
from IPython.display import display, HTML

with open("report_data_drift-80.html", "r") as f:
    display(HTML(f.read()))